In [1]:
import itertools
import matplotlib.pyplot as plt
import pandas as pd

%matplotlib inline

## Context

This notebook aims to show in which cases sklearn `auto` heuristic isn't optimal. A good default value should work well in most (if not all) regular cases. Experiments previously run explore the following settings:
- 5 datasets accounting for different data structures
- `n_samples` in `{10,000; 50,000; 100,000}`
- `n_features` in `{5, 10, 15, 20, 25, 30}`
- `algorithm` in `{'brute', 'kd_tree', 'ball_tree'}`
- `n_neighbors` in `{10, 100}`

## I - Preprocessing

Load experiments results

In [2]:
results = pd.read_csv('results.csv')
results.head()

algorithm    dataset  n_features  n_neighbors  n_samples  \
0     brute  covertype           5           10      10000   
1     brute  covertype           5           10      50000   
2     brute  covertype           5           10     100000   
3     brute  covertype           5          100      10000   
4     brute  covertype           5          100      50000   

   time_construction_mean  time_construction_std  time_querying_mean  \
0                0.000320               0.000047            1.547730   
1                0.000948               0.000045            7.257727   
2                0.001757               0.000077           14.902288   
3                0.000291               0.000008            1.625687   
4                0.000989               0.000004            7.372985   

   time_querying_std  
0           0.012124  
1           0.010302  
2           0.105015  
3           0.009813  
4           0.136214

Transform dataframe in order to get, for a given experiment, each algorithm querying time on the same row.

In [3]:
algorithms = results.algorithm.unique()
experiment_params = ['dataset', 'n_samples', 'n_features', 'n_neighbors']

for ix, algo in enumerate(algorithms):
    subset_algo = results.query('algorithm == @algo').copy()
    subset_algo.rename(columns={'time_querying_mean': algo}, inplace=True)
    subset_algo = subset_algo[experiment_params + [algo]]
    
    if ix == 0:
        df = subset_algo.copy()
    else:
        df = df.merge(subset_algo, how='inner', on=experiment_params)
    
df.head()

dataset  n_samples  n_features  n_neighbors      brute   kd_tree  \
0  covertype      10000           5           10   1.547730  0.108449   
1  covertype      50000           5           10   7.257727  0.141835   
2  covertype     100000           5           10  14.902288  0.154626   
3  covertype      10000           5          100   1.625687  0.383692   
4  covertype      50000           5          100   7.372985  0.488094   

   ball_tree  
0   0.388530  
1   0.939843  
2   1.202417  
3   0.795279  
4   1.811599

Let's check how many times each method is the fastest at querying phase.

In [4]:
time_min = df[algorithms].min(axis=1)

for algo in algorithms:
    print(f'{algo} is the fastest querying method {sum(df[algo] == time_min)} times')

brute is the fastest querying method 76 times
kd_tree is the fastest querying method 92 times
ball_tree is the fastest querying method 0 times


`'ball_tree'` is never the fastest method.

## II - Current sklearn heuristic

Quoting [sklearn meighbors documentation](https://scikit-learn.org/dev/modules/neighbors.html#choice-of-nearest-neighbors-algorithm):

> Currently, `algorithm = 'auto'` selects `'brute'` if , the input data is sparse, or `effective_metric_` isn’t in the `VALID_METRICS` list for either `'kd_tree'` or `'ball_tree'`. Otherwise, it selects the first out of `'kd_tree'` and `'ball_tree'` that has `effective_metric_` in its `VALID_METRICS` list. This choice is based on the assumption that the number of query points is at least the same order as the number of training points, and that `leaf_size` is close to its default value of `30`.

Which is translated in [sklearn source code](https://github.com/scikit-learn/scikit-learn/blob/95d4f0841/sklearn/neighbors/_base.py#L434) to:

```python
if self._fit_method == 'auto':
    # A tree approach is better for small number of neighbors,
    # and KDTree is generally faster when available
    if ((self.n_neighbors is None or
         self.n_neighbors < self._fit_X.shape[0] // 2) and
            self.metric != 'precomputed'):
        if self.effective_metric_ in VALID_METRICS['kd_tree']:
            self._fit_method = 'kd_tree'
        elif (callable(self.effective_metric_) or
                self.effective_metric_ in VALID_METRICS['ball_tree']):
            self._fit_method = 'ball_tree'
        else:
            self._fit_method = 'brute'
    else:
        self._fit_method = 'brute'
```

In the general case `n_neighbors` is smaller than `n_samples // 2` and `'kd_tree'` is choosen. We know that tree based methods suffer from high dimensionality datasets, especially when the intrinsic dimensionality is high. By not accounting for the data dimensionality, the heuristic often fail by a large margin when the data dimensionality is high. Estimating the intrinsic dimensionality is hard and costly, but `n_features` may bring information that could benefit the heuristic.

## III - K-d tree vs Brute force

Given the perimeter of the experiments, the heuristic is always `'kd_tree'` and its alternative `'brute'` (`'ball_tree'` never being the fastest). Therefor we can simplify the problem by comparing when one is better than the other.

In [5]:
params_gen = itertools.product(
    df.n_samples.unique(),
    df.n_neighbors.unique(),
)

fig, axes = plt.subplots(3, 2, figsize=(23, 20), dpi=400)
axes = axes.ravel()

std_colors = plt.rcParams['axes.prop_cycle'].by_key()['color']

xmin = df['n_features'].min()
xmax = df['n_features'].max()
ymin = df[algorithms[:2]].values.min()
ymax = df[algorithms[:2]].values.max()

for ix, (n_samples, n_neighbors) in enumerate(params_gen):
    
    for ix_color, dataset in enumerate(df.dataset.unique()):
        subset = df.query(
            'dataset == @dataset and '
            'n_samples == @n_samples and '
            'n_neighbors == @n_neighbors'
        ).copy()

        for algo, linestyle in zip(algorithms[:2], ['solid', 'dashed']):
            axes[ix].plot(
                subset['n_features'],
                subset[algo],
                color=std_colors[ix_color],
                linestyle=linestyle,
                label=f'{dataset} ({algo})'
            )
    
    axes[ix].grid(which='both', linestyle=':')
    axes[ix].legend(ncol=2, framealpha=1)
    axes[ix].set_title(f'n_samples = {n_samples:,}; n_neighbors = {n_neighbors}')
    axes[ix].set_xlabel('n_features')
    axes[ix].set_yscale('log')
    axes[ix].set_xlim(xmin, xmax)
    axes[ix].set_ylim(ymin, ymax)

fig.suptitle('K-d tree vs Brute force', fontsize=18)
plt.subplots_adjust(top=.94)

plt.savefig('img/kd_tree_vs_brute.png')

Observations:
- `'brute'` is mainly impacted by `n_samples`, data structure has little effects on it
- `'kd_tree'` is much faster with lower dataset intrinsic dimensionality or higher dataset sparsity
- `'kd_tree'` is slower when `n_neighbors` is high, in proportion to `n_samples` and `n_features`
- `'brute'` is more efficient than `'kd_tree'` when `n_features` is too high. The treshold mostly depends of the data structure and with a smaller impact from `n_samples` and `n_neighbors`

## IV - K-d tree vs Brute force — speedup ratio

In [6]:
df['speedup'] = df['kd_tree'] / df['brute']

params_gen = itertools.product(
    df.n_samples.unique(),
    df.n_neighbors.unique(),
)

fig, axes = plt.subplots(3, 2, figsize=(23, 20), dpi=400)
axes = axes.ravel()

xmin, xmax = df['n_features'].min(), df['n_features'].max()
ymin, ymax = df['speedup'].min(), df['speedup'].max()

for ix, (n_samples, n_neighbors) in enumerate(params_gen):
    
    for dataset in df.dataset.unique():
        subset = df.query(
            'dataset == @dataset and '
            'n_samples == @n_samples and '
            'n_neighbors == @n_neighbors'
        ).copy()

        axes[ix].plot(subset['n_features'], subset['speedup'], label=dataset)
    
    axes[ix].fill([xmin, xmin, xmax, xmax], [1, ymax, ymax, 1], 'mistyrose')
    axes[ix].fill([xmin, xmin, xmax, xmax], [ymin, 1, 1, ymin], 'honeydew')
    axes[ix].grid(which='both', linestyle=':')
    axes[ix].legend(loc='upper left', framealpha=1)
    axes[ix].plot([xmin, xmax], [1, 1], color='black')
    axes[ix].set_title(f'n_samples = {n_samples:,}; n_neighbors = {n_neighbors}')
    axes[ix].set_xlabel('n_features')
    axes[ix].set_yscale('log')
    axes[ix].set_xlim(xmin, xmax)
    axes[ix].set_ylim(ymin, ymax)
    axes[ix].text(xmin, 1.1, 'brute is optimal', size=10)
    axes[ix].text(xmin, .8, 'kd_tree is optimal', size=10)

fig.suptitle('K-d tree vs Brute force — speedup ratio', fontsize=18)
plt.subplots_adjust(top=.94)

plt.savefig('img/kd_tree_vs_brute_speedup_ratio.png')